In [1]:
from unsloth import FastLanguageModel
import torch

# 基础配置参数
max_seq_length = 4096 # 最大序列长度
dtype = None # 自动检测数据类型
load_in_4bit = True # 使用4位量化以减少内存使用

# 加载预训练模型和分词器
model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "workdir/model/Qwen2.5-3B-Instruct-bnb-4bit", # 选择Qwen2.5 32B指令模型
    max_seq_length = max_seq_length,
    dtype = dtype,
    load_in_4bit = load_in_4bit,
)

model = FastLanguageModel.get_peft_model(
    model,
    r = 64, # LoRA秩,控制可训练参数数量
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj",], # 需要训练的目标模块
    lora_alpha = 64, # LoRA缩放因子
    lora_dropout = 0, # LoRA dropout率
    bias = "none", # 是否训练偏置项
    use_gradient_checkpointing = "unsloth", # 使用梯度检查点节省显存
    random_state = 114514, # 随机数种子
    use_rslora = False, # 是否使用稳定版LoRA
    loftq_config = None, # LoftQ配置
)

from unsloth.chat_templates import get_chat_template
# 配置分词器使用qwen-2.5对话模板
tokenizer = get_chat_template(
    tokenizer,
    chat_template="qwen-2.5",
)


🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.


c:\Users\sbtwc\.conda\envs\unsloth_env\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Unsloth: OpenAI failed to import - ignoring for now.
🦥 Unsloth Zoo will now patch everything to make training faster!


c:\Users\sbtwc\.conda\envs\unsloth_env\Lib\site-packages\unsloth_zoo\gradient_checkpointing.py:330: UserWarning: expandable_segments not supported on this platform (Triggered internally at C:\actions-runner\_work\pytorch\pytorch\pytorch\c10/cuda/CUDAAllocatorConfig.h:28.)
  GPU_BUFFERS = tuple([torch.empty(2*256*2048, dtype = dtype, device = f"cuda:{i}") for i in range(n_gpus)])


==((====))==  Unsloth 2025.3.9: Fast Qwen2 patching. Transformers: 4.48.1.
   \\   /|    NVIDIA GeForce RTX 3060 Laptop GPU. Num GPUs = 1. Max memory: 6.0 GB. Platform: Windows.
O^O/ \_/ \    Torch: 2.6.0+cu126. CUDA: 8.6. CUDA Toolkit: 12.6. Triton: 3.2.0
\        /    Bfloat16 = TRUE. FA [Xformers = 0.0.29.post3. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


Unsloth 2025.3.9 patched 36 layers with 36 QKV layers, 36 O layers and 36 MLP layers.


In [ ]:
# 加载数据集
import json

def formatting_prompts_func(examples):
    """格式化对话数据的函数
    Args:
        examples: 包含对话列表的字典
    Returns:
        包含格式化文本的字典
    """
    questions = examples["question"]
    answer = examples["answer"]
    
    # 将Question和Response组合成对话形式
    convos = [
        [{"role": "user", "content": q}, {"role": "assistant", "content": r}]
        for q, r in zip(questions, answer)
    ]
    
    # 使用tokenizer.apply_chat_template格式化对话
    texts = [
        tokenizer.apply_chat_template(convo, tokenize=False, add_generation_prompt=False)
        for convo in convos
    ]
    
    return {"text": texts}




Map: 100%|██████████| 595/595 [00:00<00:00, 7000.21 examples/s]


In [10]:
from datasets import load_dataset
dataset = load_dataset("json", data_files="workdir\dataset\dataset.json",split="train")
dataset = dataset.map(formatting_prompts_func, batched = True)

print(dataset[5])

{'question': 'LLaMA-Factory有哪些训练方法？', 'answer': 'LLaMA-Factory提供了Pre-training和Post-training两种训练方法。', 'text': '<|im_start|>system\nYou are Qwen, created by Alibaba Cloud. You are a helpful assistant.<|im_end|>\n<|im_start|>user\nLLaMA-Factory有哪些训练方法？<|im_end|>\n<|im_start|>assistant\nLLaMA-Factory提供了Pre-training和Post-training两种训练方法。<|im_end|>\n'}


In [13]:
from trl import SFTTrainer
from transformers import TrainingArguments, DataCollatorForSeq2Seq
from unsloth import is_bfloat16_supported

# 配置训练器
trainer = SFTTrainer(
    model=model,
    tokenizer=tokenizer,
    train_dataset=dataset,
    dataset_text_field="text",
    max_seq_length=max_seq_length,
    data_collator=DataCollatorForSeq2Seq(tokenizer=tokenizer),
    dataset_num_proc=1,
    packing=False,
    args=TrainingArguments(
        per_device_train_batch_size=1, # 每个设备的批次大小
        gradient_accumulation_steps=4, # 梯度累积步数
        warmup_steps=3*50, # 预热步数
        max_steps=3*500, # 最大训练步数
        learning_rate=1e-4, # 学习率
        fp16=not is_bfloat16_supported(), # 是否使用fp16
        bf16=is_bfloat16_supported(), # 是否使用bf16
        logging_steps=5, # 日志记录间隔
        optim="paged_adamw_8bit", # 优化器
        weight_decay=0.01, # 权重衰减
        lr_scheduler_type="linear", # 学习率调度器
        seed=114514, # 随机种子
        output_dir="workdir/checkpoint/", # 输出目录
        save_strategy="steps",  # 按步保存中间权重
        save_steps=200,  # 每多少步保存一次中间权重
        report_to="none", # 不使用外部日志工具
    ),
)

from unsloth.chat_templates import train_on_responses_only
# 设置仅对助手回复部分计算损失
trainer = train_on_responses_only(
    trainer,
    instruction_part = "<|im_start|>user\n",
    response_part = "<|im_start|>assistant\n",
)

# 获取GPU信息
gpu_stats = torch.cuda.get_device_properties(0)
start_gpu_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
max_memory = round(gpu_stats.total_memory / 1024 / 1024 / 1024, 3)
print(f"GPU = {gpu_stats.name}. Max memory = {max_memory} GB.")
print(f"{start_gpu_memory} GB of memory reserved.")

GPU = NVIDIA GeForce RTX 3060 Laptop GPU. Max memory = 6.0 GB.
2.557 GB of memory reserved.


In [15]:
#trainer_stats = trainer.train()
trainer_stats = trainer.train(resume_from_checkpoint = False)


==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 595 | Num Epochs = 11 | Total steps = 1,500
O^O/ \_/ \    Batch size per device = 1 | Gradient accumulation steps = 4
\        /    Data Parallel GPUs = 1 | Total batch size (1 x 4 x 1) = 4
 "-____-"     Trainable parameters = 119,734,272/1,818,406,912 (6.58% trained)


In [18]:
FastLanguageModel.for_inference(model)

# 准备相同的测试输入
messages = [
    {"role": "user", "content": 
     """llama factory支持什么类型的微调"""}
]
inputs = tokenizer.apply_chat_template(
    messages,
    tokenize = True,
    add_generation_prompt = True,
    return_tensors = "pt",
).to("cuda")

# 使用TextStreamer进行流式生成
from transformers import TextStreamer
text_streamer = TextStreamer(tokenizer, skip_prompt = True)
_ = model.generate(input_ids = inputs, streamer = text_streamer, max_new_tokens = 128,
                   use_cache = True, temperature = 1.5, min_p = 0.1)

llamafactory支持多种类型的微调，具体支持的类型可以通过配置文件的`finetuning_type`字段来指定。例如，在`examples/inference/llamafactory_lora_sft.yaml`配置文件中，`finetuning_type`指定为`lora`，表示使用LoRA微调方法。<|im_end|>
